# AutoTrain

## Imports

In [1]:
import os
import subprocess

import yaml

## Config

In [2]:
from huggingface_hub import login, get_token, whoami
login()

### Template
Im creating a template so we can iterate through each of our experiments.

Here you can see a few design decisions:
- We leave `project_name` and `text_column` empty to overwrite later per experiment
- We log in tensorboard, you can use wandb, but you will need to install it in the AutoTrain env that is run on spaces, which gets complex
- I choose an `l4x1` from [these options](https://github.com/huggingface/autotrain-advanced/blob/2d787b2033414d06f1e9be2ea0caacad3097f5e8/src/autotrain/backends/base.py#L21)
    - This is a [well priced](https://huggingface.co/pricing#spaces) way of training a 7B moodel 
    - It's very efficient as well at 24GB VRAM
- It's becoming less common to use a `valid_split` 
- I run 2 epochs as the loss still decreases steadily, but some say for LoRAs you should just do 1
- Its a good idea use `all-linear` when using LoRA 

In [3]:
# Base config
config_template = {
    "task": "llm-sft",
    "base_model": "tiiuae/Falcon3-7B-Instruct",
    "project_name": "",
    "log": "tensorboard",
    "backend": "spaces-a100-large",
    "data": {
        "path": "derek-thomas/labeled-multiple-choice-explained-falcon-tokenized",
        "train_split": "train",
        "valid_split": None,
        "chat_template": "tokenizer",
        "column_mapping": {
            "text_column": ""
            },
        },
    "params": {
        "block_size": 512,
        "model_max_length": 1750,
        "epochs": 4,
        "batch_size": 8,
        "lr": 5e-5,
        "peft": True,
        "quantization": "int4",
        "target_modules": "all-linear",
        "padding": "right",
        "optimizer": "adamw_torch",
        "scheduler": "linear",
        "gradient_accumulation": 8,
        "mixed_precision": "bf16",
        },
    "hub": {
        "username": "derek-thomas",
        "token": get_token(),
        "push_to_hub": True,
        },
}

### Experiments
Here we choose the `project_name` and `text_column` for each experiment.

In [4]:
project_suffixes = ["RFA-gpt3-5", "RFA-falcon", "FAR-gpt3-5", "FAR-falcon", "FA"]
text_columns = ["conversation_RFA_gpt3_5", "conversation_RFA_falcon", "conversation_FAR_gpt3_5",
                "conversation_FAR_falcon", "conversation_FA"]

Directory to store generated configs

In [5]:
output_dir = "./autotrain_configs"
os.makedirs(output_dir, exist_ok=True)

## AutoTrain for each Experiment

In [6]:
# Generate configs and run commands
autotrain_spaces = []
autotrain_models = []
for project_suffix, text_column in zip(project_suffixes, text_columns):
    # Modify the config
    config = config_template.copy()
    config["project_name"] = f"falcon-v03-poe-{project_suffix}"
    config["data"]["column_mapping"]["text_column"] = text_column

    # Save the config to a YAML file
    config_path = os.path.join(output_dir, f"{text_column}.yml")
    with open(config_path, "w") as f:
        yaml.dump(config, f)

    # # Run the command
    print(f"Running autotrain with config: {config_path}")
    subprocess.run(["autotrain", "--config", config_path])

    space_name = f"{whoami()['name']}/autotrain-{config['project_name']}"
    model_name = f"{whoami()['name']}/{config['project_name']}"
    autotrain_spaces.append(space_name)
    autotrain_models.append(model_name)
    print(f'\n---\nhttps://huggingface.co/spaces/{space_name}\n---\n')

Running autotrain with config: ./autotrain_configs/conversation_RFA_gpt3_5.yml
INFO     | 2025-01-10 13:45:51 | autotrain.cli.autotrain:main:58 - Using AutoTrain configuration: ./autotrain_configs/conversation_RFA_gpt3_5.yml
INFO     | 2025-01-10 13:45:51 | autotrain.parser:__post_init__:165 - Running task: lm_training
INFO     | 2025-01-10 13:45:51 | autotrain.parser:__post_init__:166 - Using backend: spaces-a100-large
INFO     | 2025-01-10 13:45:51 | autotrain.parser:run:224 - {'model': 'tiiuae/Falcon3-7B-Instruct', 'project_name': 'falcon-v03-poe-RFA-gpt3-5', 'data_path': 'derek-thomas/labeled-multiple-choice-explained-falcon-tokenized', 'train_split': 'train', 'valid_split': None, 'add_eos_token': True, 'block_size': 512, 'model_max_length': 1750, 'padding': 'right', 'trainer': 'sft', 'use_flash_attention_2': False, 'log': 'tensorboard', 'disable_gradient_checkpointing': False, 'logging_steps': -1, 'eval_strategy': 'epoch', 'save_total_limit': 1, 'auto_find_batch_size': False, 'mix

# Cleanup

In [9]:
from huggingface_hub import HfApi
api = HfApi()

In [7]:
from pprint import pprint
pprint(autotrain_spaces)
print()
pprint(autotrain_models)

['derek-thomas/autotrain-falcon-v03-poe-RFA-gpt3-5',
 'derek-thomas/autotrain-falcon-v03-poe-RFA-falcon',
 'derek-thomas/autotrain-falcon-v03-poe-FAR-gpt3-5',
 'derek-thomas/autotrain-falcon-v03-poe-FAR-falcon',
 'derek-thomas/autotrain-falcon-v03-poe-FA']

['derek-thomas/falcon-v03-poe-RFA-gpt3-5',
 'derek-thomas/falcon-v03-poe-RFA-falcon',
 'derek-thomas/falcon-v03-poe-FAR-gpt3-5',
 'derek-thomas/falcon-v03-poe-FAR-falcon',
 'derek-thomas/falcon-v03-poe-FA']


<span style="color:red; font-size:20px; font-weight:bold;">
WAIT TO RUN THIS UNTIL YOUR SPACES ARE FINISHED TRAINING!
</span>

In [10]:
for space in autotrain_spaces:
    confirm = input(f"Are you sure you want to delete the space '{space}'? (y/n): ")
    if confirm.lower() == 'y':
        api.delete_repo(space, repo_type='space')
        print(f"Deleted {space}")
    else:
        print(f"Skipped {space}")


Are you sure you want to delete the space 'derek-thomas/autotrain-falcon-v03-poe-RFA-gpt3-5'? (y/n):  y


Deleted derek-thomas/autotrain-falcon-v03-poe-RFA-gpt3-5


Are you sure you want to delete the space 'derek-thomas/autotrain-falcon-v03-poe-RFA-falcon'? (y/n):  y


Deleted derek-thomas/autotrain-falcon-v03-poe-RFA-falcon


Are you sure you want to delete the space 'derek-thomas/autotrain-falcon-v03-poe-FAR-gpt3-5'? (y/n):  y


Deleted derek-thomas/autotrain-falcon-v03-poe-FAR-gpt3-5


Are you sure you want to delete the space 'derek-thomas/autotrain-falcon-v03-poe-FAR-falcon'? (y/n):  y


Deleted derek-thomas/autotrain-falcon-v03-poe-FAR-falcon


Are you sure you want to delete the space 'derek-thomas/autotrain-falcon-v03-poe-FA'? (y/n):  y


Deleted derek-thomas/autotrain-falcon-v03-poe-FA


<span style="color:red; font-size:20px; font-weight:bold;">
ONLY RUN THIS IF YOU NEED TO RESTART FROM SCRATCH
THIS WILL DELETE YOUR MODELS
</span>


In [11]:
for model in autotrain_models:
    confirm = input(f"Are you sure you want to delete the model '{model}'? (y/n): ")
    if confirm.lower() == 'y':
        api.delete_repo(model, repo_type='model')
        print(f"Deleted {model}")
    else:
        print(f"Skipped {model}")


Are you sure you want to delete the model 'derek-thomas/falcon-v03-poe-RFA-gpt3-5'? (y/n):  y


Deleted derek-thomas/falcon-v03-poe-RFA-gpt3-5


Are you sure you want to delete the model 'derek-thomas/falcon-v03-poe-RFA-falcon'? (y/n):  y


Deleted derek-thomas/falcon-v03-poe-RFA-falcon


Are you sure you want to delete the model 'derek-thomas/falcon-v03-poe-FAR-gpt3-5'? (y/n):  y


Deleted derek-thomas/falcon-v03-poe-FAR-gpt3-5


Are you sure you want to delete the model 'derek-thomas/falcon-v03-poe-FAR-falcon'? (y/n):  y


Deleted derek-thomas/falcon-v03-poe-FAR-falcon


Are you sure you want to delete the model 'derek-thomas/falcon-v03-poe-FA'? (y/n):  y


Deleted derek-thomas/falcon-v03-poe-FA


In [12]:
from huggingface_hub import move_repo

for model in autotrain_models:
    user, model_tag = model.split('/')
    to = f"{user}/{model_tag}_backup"
    confirm = input(f"Are you sure you want to move the model from '{model}' to {to}? (y/n): ")
    if confirm.lower() == 'y':
        move_repo(from_id=model, to_id=to)
        print(f"Moved {model} to {to}")
    else:
        print(f"Skipped {model}")

Are you sure you want to move the model from 'derek-thomas/falcon-v03-poe-RFA-gpt3-5' to derek-thomas/falcon-v03-poe-RFA-gpt3-5_backup? (y/n):  y


Moved derek-thomas/falcon-v03-poe-RFA-gpt3-5 to derek-thomas/falcon-v03-poe-RFA-gpt3-5_backup


Are you sure you want to move the model from 'derek-thomas/falcon-v03-poe-RFA-falcon' to derek-thomas/falcon-v03-poe-RFA-falcon_backup? (y/n):  y


Moved derek-thomas/falcon-v03-poe-RFA-falcon to derek-thomas/falcon-v03-poe-RFA-falcon_backup


Are you sure you want to move the model from 'derek-thomas/falcon-v03-poe-FAR-gpt3-5' to derek-thomas/falcon-v03-poe-FAR-gpt3-5_backup? (y/n):  y


Moved derek-thomas/falcon-v03-poe-FAR-gpt3-5 to derek-thomas/falcon-v03-poe-FAR-gpt3-5_backup


Are you sure you want to move the model from 'derek-thomas/falcon-v03-poe-FAR-falcon' to derek-thomas/falcon-v03-poe-FAR-falcon_backup? (y/n):  y


Moved derek-thomas/falcon-v03-poe-FAR-falcon to derek-thomas/falcon-v03-poe-FAR-falcon_backup


Are you sure you want to move the model from 'derek-thomas/falcon-v03-poe-FA' to derek-thomas/falcon-v03-poe-FA_backup? (y/n):  y


Moved derek-thomas/falcon-v03-poe-FA to derek-thomas/falcon-v03-poe-FA_backup
